# SmolLM2와 함께 대화 템플릿 탐색하기

이 노트북은 `SmolLM2` 모델과 함께 대화 템플릿을 사용하는 방법을 설명합니다. 대화 템플릿은 사용자와 AI 모델 간의 상호작용을 구조화하여, 일관되고 맥락에 맞는 응답을 보장합니다.

In [ ]:
# Google Colab에서 requirements 설치
# !pip install transformers datasets trl huggingface_hub

# Hugging Face 인증
from huggingface_hub import login

login()

# 허브 토큰을 HF_TOKEN 환경 변수로 설정해두면 편하게 사용할 수 있습니다.

In [ ]:
# 주요 라이브러리 불러오기
from transformers import AutoModelForCausalLM, AutoTokenizer
from trl import setup_chat_format
import torch

## SmolLM2 대화 템플릿

`SmolLM2` 모델에서 대화 템플릿을 사용하는 법을 알아봅시다. 간단한 대화를 정의하고 대화 템플릿을 적용해보겠습니다.

In [ ]:
# 동적으로 디바이스 설정
device = (
    "cuda"
    if torch.cuda.is_available()
    else "mps" if torch.backends.mps.is_available() else "cpu"
)

model_name = "HuggingFaceTB/SmolLM2-135M"
model = AutoModelForCausalLM.from_pretrained(
    pretrained_model_name_or_path=model_name
).to(device)
tokenizer = AutoTokenizer.from_pretrained(pretrained_model_name_or_path=model_name)
model, tokenizer = setup_chat_format(model=model, tokenizer=tokenizer)

In [ ]:
# SmolLM2를 위한 메시지 정의
messages = [
    {"role": "user", "content": "Hello, how are you?"},
    {
        "role": "assistant",
        "content": "I'm doing well, thank you! How can I assist you today?",
    },
]

# 토큰화 없이 대화 템플릿 적용하기

토크나이저는 사용자와 어시스턴트의 역할을 설명하기 위해 특수 토큰이 포함된 문자열로 대화를 표현합니다.

In [5]:
input_text = tokenizer.apply_chat_template(messages, tokenize=False)

print("Conversation with template:", input_text)

Conversation with template: <|im_start|>user
Hello, how are you?<|im_end|>
<|im_start|>assistant
I'm doing well, thank you! How can I assist you today?<|im_end|>



# 대화 디코딩

대화 내용은 위와 같지만 추가적인 어시스턴트 메시지가 표시됩니다.

In [ ]:
input_text = tokenizer.apply_chat_template(
    messages, tokenize=True, add_generation_prompt=True
)

print("Conversation decoded:", tokenizer.decode(token_ids=input_text))

Conversation decoded: <|im_start|>user
Hello, how are you?<|im_end|>
<|im_start|>assistant
I'm doing well, thank you! How can I assist you today?<|im_end|>
<|im_start|>assistant



# 대화 토크나이징

물론, 토크나이저는 대화와 특수 토큰을 모델의 단어 사전(vocabulary)과 관련된 아이디로 토큰화 하기도 합니다.


In [7]:
input_text = tokenizer.apply_chat_template(messages, add_generation_prompt=True)

print("Conversation tokenized:", input_text)

Conversation tokenized: [1, 4093, 198, 19556, 28, 638, 359, 346, 47, 2, 198, 1, 520, 9531, 198, 57, 5248, 2567, 876, 28, 9984, 346, 17, 1073, 416, 339, 4237, 346, 1834, 47, 2, 198, 1, 520, 9531, 198]


<div style='background-color: lightblue; padding: 10px; border-radius: 5px; margin-bottom: 20px; color:black'>
    <h2 style='margin: 0;color:blue'>연습: SFT를 위한 데이터 가공하기</h2>
    <p>Hugging Face 허브에서 데이터셋을 가져온 후 SFT를 적용할 수 있게 가공해보세요.</p>
    <p><b>난이도</b></p>
    <p>🐢 `HuggingFaceTB/smoltalk` 데이터셋을 chatml 형식으로 변환하기</p>
    <p>🐕 `openai/gsm8k` 데이터셋을 chatml 형식으로 변환하기</p>
</div>

In [ ]:
from IPython.core.display import display, HTML

display(
    HTML(
        """<iframe
  src="https://huggingface.co/datasets/HuggingFaceTB/smoltalk/embed/viewer/all/train?row=0"
  frameborder="0"
  width="100%"
  height="360px"
></iframe>
"""
    )
)

In [ ]:
from datasets import load_dataset

ds = load_dataset("HuggingFaceTB/smoltalk", "everyday-conversations")


def process_dataset(sample):
    # TODO: 🐢 예시를 대화 형식으로 변환하기
    # 대화 템플릿을 적용하기 위해 토크나이저 메서드를 사용하세요.
    return sample


ds = ds.map(process_dataset)

In [ ]:
display(
    HTML(
        """<iframe
  src="https://huggingface.co/datasets/openai/gsm8k/embed/viewer/main/train"
  frameborder="0"
  width="100%"
  height="360px"
></iframe>
"""
    )
)

In [ ]:
ds = load_dataset("openai/gsm8k", "main")


def process_dataset(sample):
    # TODO: 🐕 예시를 대화 형식으로 변환하기

    # 1. role과 content를 이용해 메시지 형식을 만들어보세요.

    # 2. 토크나이저 메서드를 활용해 예시에 대화 템플릿을 적용해보세요.

    return sample


ds = ds.map(process_dataset)

## 결론

이 노트북에서는 `SmolLM2`와 같은 다양한 모델에 대화 템플릿을 적용하는 방법을 보여주었습니다. 대화 템플릿을 통해 사용자와 AI 모델 사이 상호작용을 구조화함으로써 모델이 일관되고 맥락에 맞는 응답을 제공하도록 할 수 있습니다.

실습을 통해 데이터셋을 ChatML 형식으로 변환해보았습니다. TRL이 이를 자동으로 처리해주지만, 내부 작동 방식을 이해해두는 것도 유용합니다.